# Data Cleanup

## Necessary Steps

1. Understand the data structure: Look through the database, understand the main structure, i.e., what each row represents, and what columns and types of information are available
2. Merge game file to add in week identifier to the new dataset (games.csv is in '1. Additional Data File')
3. Create column categorizations to filter dataset for relevant purposes
4. Break down receiver into its individual row
5. Create playmaker column, and check id uniqueness - check that one ID corresponds to one name
6. Flag non-relevant plays - add a binary column that flags 1 for run, pass, reception, FG/XP, 0 for all others
7. Add any additional stat needed - reception (for plays that fall under 'reception'), target ('reception', 'pass')
8. Add position based off of the highest stat of a player. Position will be refined later with web scraping
9. Ensure that stat are correctly represented for a given position
10. Verify top 50 stats against the reported ones


## Setup Environment

In [9]:
import pandas as pd
import numpy as np
from pandas import ExcelWriter
pd.set_option('display.max_columns', None)

## 1. Upload Data

In [ ]:
'''
Not sure why your folder names were changes. The working directory of this file is where its source code is located
so you can specify directories relatively
'''

In [10]:
# Store your files in the same folder as the source code, so you don't have to specify the directory
df_file_2019 = "../../1. Raw-Data/data2019.csv"
df_file_game = "../1. Additional-Data/games.csv"

# Use the convention df for dataframes
df1 = pd.read_csv(df_file_2019)
df_games = pd.read_csv(df_file_game)

In [54]:
df1

## 2. Add in Weekly Identifier

In [ ]:
'''
In each play row the week of that game will be displayed as a new column.
This will be done through a merge along the game_id column from the game.csv file. 
'''

In [11]:
df = df1.merge(df_games[["game_id", "week"]], on = 'game_id')

df

Unnamed: 0  play_id     game_id home_team away_team posteam  \
0               1       35  2019090500       CHI        GB      GB   
1               2       50  2019090500       CHI        GB      GB   
2               3       71  2019090500       CHI        GB      GB   
3               4       95  2019090500       CHI        GB      GB   
4               5      125  2019090500       CHI        GB      GB   
...           ...      ...         ...       ...       ...     ...   
45541       45542     3955  2019122915       SEA        SF     SEA   
45542       45543     3977  2019122915       SEA        SF     SEA   
45543       45544     3999  2019122915       SEA        SF     SEA   
45544       45545     4080  2019122915       SEA        SF      SF   
45545       45546     4101  2019122915       SEA        SF     NaN   

      posteam_type defteam side_of_field  yardline_100   game_date  \
0             away     CHI           CHI          35.0  2019-09-05   
1             away     CHI            GB          75.0  2019-09-05   
2             away     CHI            GB          75.0  2019-09-05   
3             away     CHI            GB          75.0  2019-09-05   
4             away     CHI            GB          85.0  2019-09-05   
...            ...     ...           ...           ...         ...   
45541         home      SF            SF           5.0  2019-12-29   
45542         home      SF            SF           5.0  2019-12-29   
45543         home      SF            SF           5.0  2019-12-29   
45544         away     SEA            SF          99.0  2019-12-29   
45545          NaN     NaN            SF           NaN  2019-12-29   

       quarter_seconds_remaining  half_seconds_remaining  \
0                          900.0                  1800.0   
1                          900.0                  1800.0   
2                          873.0                  1773.0   
3                          825.0                  1725.0   
4                          795.0                  1695.0   
...                          ...                     ...   
45541                       22.0                    22.0   
45542                       15.0                    15.0   
45543                       12.0                    12.0   
45544                        9.0                     9.0   
45545                        0.0                     0.0   

       game_seconds_remaining game_half  quarter_end  drive  sp  qtr  down  \
0                      3600.0     Half1            0      1   0    1   NaN   
1                      3600.0     Half1            0      1   0    1   1.0   
2                      3573.0     Half1            0      1   0    1   2.0   
3                      3525.0     Half1            0      1   0    1   3.0   
4                      3495.0     Half1            0      1   0    1   4.0   
...                       ...       ...          ...    ...  ..  ...   ...   
45541                    22.0     Half2            0     16   0    4   2.0   
45542                    15.0     Half2            0     16   0    4   3.0   
45543                    12.0     Half2            0     16   0    4   4.0   
45544                     9.0     Half2            0     17   0    4   1.0   
45545                     0.0     Half2            1     17   0    4   NaN   

       goal_to_go   time   yrdln  ydstogo  ydsnet  \
0             0.0  15:00  CHI 35        0     -10   
1             0.0  15:00   GB 25       10     -10   
2             0.0  14:33   GB 25       10     -10   
3             0.0  13:45   GB 25       10     -10   
4             0.0  13:15   GB 15       20     -10   
...           ...    ...     ...      ...     ...   
45541         1.0  00:22    SF 5        5      72   
45542         1.0  00:15    SF 5        5      72   
45543         1.0  00:12    SF 5        5      72   
45544         0.0  00:09    SF 1       10       2   
45545         NaN  00:00    SF 1        0       2   

                              

## 3. Create Categorization Lists

In [ ]:
'''
The columns in the 2019 data file are arranged into categorical lists.
Many of the lists can be automated due to the presence of key words in their title.
'''

### 3.1 Main Lists

In [56]:

key = ['Flag', 'Playmaker_id', 'Playmaker_name', 'play_id', 'game_id', 'home_team', 'away_team', 'week', 'game_date', 'posteam', 'posteam_type', 'defteam', 'side_of_field', 'play_type']


pass_play = ['pass_length','pass_location','air_yards']
run_play = ['run_location', 'run_gap']
yard_info = ['yrdln','ydstogo','ydsnet','yards_gained', "fumble_recovery_1_yards", "fumble_recovery_2_yards", "return_yards"]

receiver_info = [col for col in df.columns if 'receiver' in col]
receiver_info += ['yards_after_catch', 'incomplete_pass', 'complete_pass', 'touchdown', 'pass_touchdown', 'fumble_lost', 'Playmaker_id', 'Playmaker_name']


passer_info = [col for col in df.columns if 'passer' in col]


passer_info += ['yards_after_catch', 'incomplete_pass', 'complete_pass', 'touchdown', 'pass_touchdown', 'fumble_lost', 'Playmaker_id', 'Playmaker_name', 'interception']


rusher_info = [col for col in df.columns if 'rusher' in col]
rusher_info += ['touchdown', 'fumble_lost', 'Playmaker_id', 'Playmaker_name']

two_pt_con


xp = ['field_goal_result', 'kick_distance', 'extra_point_result', 'kicker_']



### 3.2 Other Lists

In [57]:

game_time_info = ['quarter_seconds_remaining', 'half_seconds_remaining', 'game_seconds_remaining', 'game_half', 'quarter_end', 'time']

gen_play_info = ['drive', 'sp', 'down', 'goal_to_go','desc','play_type','shotgun','no_huddle','qb_dropback','qb_kneel','qb_spike','qb_scramble']

team_info = ["return_team", 'td_team', 'posteam_time', 'defteam_time', 'total_home_score','total_away_score', 'posteam_score_post','defteam_score_post', 'score_differential', "forced_fumble_player_1_team", "forced_fumble_player_2_team", "solo_tackle_1_team", "solo_tackle_2_team", "assist_tackle_1_team", "assist_tackle_2_team", "assist_tackle_3_team", "assist_tackle_4_team", "fumbled_1_team", "fumbled_2_team", "fumble_recovery_1_team", "fumble_recovery_2_team"]

game_info = ['play_id','game_id','home_team','away_team','posteam','posteam_type', 'defteam', 'side_of_field', 'yardline_100','game_date', "year"]


prob_cols = [col for col in df.columns if 'prob' in col]

penalty_info = [col for col in df.columns if 'penalty' in col]


kickoff_punt_info = [col for col in df.columns if 'kickoff' in col]

kickoff_punt_info += [col for col in df.columns if 'kicker' in col]
kickoff_punt_info += [col for col in df.columns if 'punt' in col]


defensive_info = [col for col in df.columns if 'defensive' in col]

defensive_info += [col for col in df.columns if 'fumble' in col]
defensive_info += [col for col in df.columns if 'sack' in col]
defensive_info += [col for col in df.columns if 'interception' in col]
defensive_info += [col for col in df.columns if 'defense' in col]

epa_info = [col for col in df.columns if 'epa' in col]

wpa_info = [col for col in df.columns if 'wpa' in col]

touchdown_info = [col for col in df.columns if 'touchdown' in col]

timeout_info = [col for col in df.columns if 'timeout' in col]

wp_info = [col for col in df.columns if 'wp' in col]

score_info = [col for col in df.columns if 'score' in col]

tackle_info = [col for col in df.columns if 'tackle' in col]

all_lists = [game_info, team_info, game_time_info ,xp, wpa_info, epa_info, touchdown_info, yard_info, run_play, pass_play, key, prob_cols, penalty_info, kickoff_punt_info, defensive_info, timeout_info, passer_info, receiver_info, rusher_info, score_info, tackle_info]

big_list = [item for elem in all_lists for item in elem]

remainder_list = [col for col in df.columns if col not in big_list]

['passer_player_id',
 'passer_player_name',
 'interception',
 'interception_player_id',
 'interception_player_name',
 'lateral_interception_player_id',
 'lateral_interception_player_name',
 'yards_after_catch',
 'incomplete_pass',
 'complete_pass',
 'touchdown',
 'pass_touchdown',
 'fumble']

## 4. Receiver row creation

In [ ]:
'''
For each pass play, creat an additional row for the recepetion
so that there can be two play makers (the passer and the receiver).
'''

In [14]:
new_df = pd.DataFrame()
new_df = df[(df['play_type']=="pass")]

new_df['play_type'].replace({'pass': 'reception'}, inplace=True)

df = pd.concat([df, new_df], sort= True)

df

Unnamed: 0          Zone   air_epa   air_wpa  air_yards  assist_tackle  \
0               1         Other       NaN       NaN        NaN            0.0   
1               2         Other       NaN       NaN        NaN            0.0   
2               3         Other -1.095212 -0.031647       -1.0            0.0   
3               4         Other       NaN       NaN        NaN            0.0   
4               5         Other       NaN       NaN        NaN            0.0   
...           ...           ...       ...       ...        ...            ...   
45535       45536      Red Zone  4.335141  0.657133       12.0            0.0   
45538       45539      Red Zone  3.532878  0.610825       11.0            0.0   
45541       45542  Inside the 5  2.888636  0.702366        5.0            0.0   
45542       45543  Inside the 5  3.550080  0.899287        5.0            0.0   
45543       45544  Inside the 5 -2.636491  0.010686        4.0            0.0   

      assist_tackle_1_player_id assist_tackle_1_player_name  \
0                           NaN                         NaN   
1                           NaN                         NaN   
2                           NaN                         NaN   
3                           NaN                         NaN   
4                           NaN                         NaN   
...                         ...                         ...   
45535                       NaN                         NaN   
45538                       NaN                         NaN   
45541                       NaN                         NaN   
45542                       NaN                         NaN   
45543                       NaN                         NaN   

      assist_tackle_1_team assist_tackle_2_player_id  \
0                      NaN                       NaN   
1                      NaN                       NaN   
2                      NaN                       NaN   
3                      NaN                       NaN   
4                      NaN                       NaN   
...                    ...                       ...   
45535                  NaN                       NaN   
45538                  NaN                       NaN   
45541                  NaN                       NaN   
45542                  NaN                       NaN   
45543                  NaN                       NaN   

      assist_tackle_2_player_name assist_tackle_2_team  \
0                             NaN                  NaN   
1                             NaN                  NaN   
2                             NaN                  NaN   
3                             NaN                  NaN   
4                             NaN                  NaN   
...                           ...                  ...   
45535                         NaN                  NaN   
45538                         NaN                  NaN   
45541                         NaN                  NaN   
45542                         NaN                  NaN   
45543                         NaN                  NaN   

      assist_tackle_3_player_id assist_tackle_3_player_name  \
0                           NaN                         NaN   
1                           NaN                         NaN   
2                           NaN                         NaN   
3                           NaN                         NaN   
4                           NaN                         NaN   
...                         ...                         ...   
45535                       NaN                         NaN   
45538                       NaN                         NaN   
45541                       NaN                         NaN   
45542                       NaN                         NaN   
45543                       NaN                         NaN   

      assist_tackle_3_team assist_tackle_4_player_id  \
0                      NaN                       NaN   
1                      NaN            

## 5. Playmaker Column

In [ ]:
'''
Step 5 creates a playmaker column, and also checks if each player 
id matchs only one name and corrects those that do not.

Steven's approach starts by establishing a playmaker id and name column and uses these columns to identify 
which ids have more than one name.

Using grouby you can cross check the playmake_id column and the playmaker_name column and isolate that id that have 
more than one name.

'''

#### 5.1 Define Play Maker

In [16]:

df['play_maker_id'] = np.where(df['play_type']=='run',df['rusher_player_id'], np.NaN)
df['play_maker_id'] = np.where(df['play_type']=='pass', df['passer_player_id'], df['play_maker'])
df['play_maker_id'] = np.where(df['play_type']=='reception',df['receiver_player_id'],df['play_maker'])
df['play_maker_id'] = np.where((df['play_type']=='extra_point')|(df['play_type']=='field_goal'),df['kicker_player_id'],df['play_maker'])

df[df['play_type'] == 'run']

Unnamed: 0      Zone  air_epa  air_wpa  air_yards  assist_tackle  \
1               2     Other      NaN      NaN        NaN            0.0   
6               7     Other      NaN      NaN        NaN            1.0   
8               9     Other      NaN      NaN        NaN            0.0   
10             11     Other      NaN      NaN        NaN            0.0   
14             15     Other      NaN      NaN        NaN            0.0   
...           ...       ...      ...      ...        ...            ...   
45513       45514     Other      NaN      NaN        NaN            0.0   
45515       45516  Red Zone      NaN      NaN        NaN            0.0   
45519       45520     Other      NaN      NaN        NaN            0.0   
45520       45521     Other      NaN      NaN        NaN            0.0   
45544       45545     Other      NaN      NaN        NaN            0.0   

      assist_tackle_1_player_id assist_tackle_1_player_name  \
1                           NaN                         NaN   
6                    00-0033120                     K.Clark   
8                           NaN                         NaN   
10                          NaN                         NaN   
14                          NaN                         NaN   
...                         ...                         ...   
45513                       NaN                         NaN   
45515                       NaN                         NaN   
45519                       NaN                         NaN   
45520                       NaN                         NaN   
45544                       NaN                         NaN   

      assist_tackle_1_team assist_tackle_2_player_id  \
1                      NaN                       NaN   
6                       GB                00-0032412   
8                      NaN                       NaN   
10                     NaN                       NaN   
14                     NaN                       NaN   
...                    ...                       ...   
45513                  NaN                       NaN   
45515                  NaN                       NaN   
45519                  NaN                       NaN   
45520                  NaN                       NaN   
45544                  NaN                       NaN   

      assist_tackle_2_player_name assist_tackle_2_team  \
1                             NaN                  NaN   
6                         D.Lowry                   GB   
8                             NaN                  NaN   
10                            NaN                  NaN   
14                            NaN                  NaN   
...                           ...                  ...   
45513                         NaN                  NaN   
45515                         NaN                  NaN   
45519                         NaN                  NaN   
45520                         NaN                  NaN   
45544                         NaN                  NaN   

      assist_tackle_3_player_id assist_tackle_3_player_name  \
1                           NaN                         NaN   
6                           NaN                         NaN   
8                           NaN                         NaN   
10                          NaN                         NaN   
14                          NaN                         NaN   
...                         ...                         ...   
45513                       NaN                         NaN   
45515                       NaN                         NaN   
45519                       NaN                         NaN   
45520                       NaN                         NaN   
45544                       NaN                         NaN   

      assist_tackle_3_team assist_tackle_4_player_id  \
1                      NaN                       NaN   
6                      NaN                       NaN   
8                      NaN                       NaN  

In [15]:
# Add in corresponding play maker ID
df['play_maker'] = np.where(df['play_type']=='run', df['rusher_player_name'], np.NaN)
df['play_maker'] = np.where(df['play_type']=='pass',df['passer_player_name'], df['play_maker'])
df['play_maker'] = np.where((df['play_type']=='no_play') & (df['interception']== 1), df['passer_player_name'], df['play_maker'])
df['play_maker'] = np.where(df['play_type']=='reception',df['receiver_player_name'],df['play_maker'])
df['play_maker'] = np.where((df['play_type']=='extra_point')|(df['play_type']=='field_goal'),df['kicker_player_name'],df['play_maker'])
df
# Now that we have a single column to identify play makers, it is a lot easier to check for ID uniqueness

Unnamed: 0          Zone   air_epa   air_wpa  air_yards  assist_tackle  \
0               1         Other       NaN       NaN        NaN            0.0   
1               2         Other       NaN       NaN        NaN            0.0   
2               3         Other -1.095212 -0.031647       -1.0            0.0   
3               4         Other       NaN       NaN        NaN            0.0   
4               5         Other       NaN       NaN        NaN            0.0   
...           ...           ...       ...       ...        ...            ...   
45535       45536      Red Zone  4.335141  0.657133       12.0            0.0   
45538       45539      Red Zone  3.532878  0.610825       11.0            0.0   
45541       45542  Inside the 5  2.888636  0.702366        5.0            0.0   
45542       45543  Inside the 5  3.550080  0.899287        5.0            0.0   
45543       45544  Inside the 5 -2.636491  0.010686        4.0            0.0   

      assist_tackle_1_player_id assist_tackle_1_player_name  \
0                           NaN                         NaN   
1                           NaN                         NaN   
2                           NaN                         NaN   
3                           NaN                         NaN   
4                           NaN                         NaN   
...                         ...                         ...   
45535                       NaN                         NaN   
45538                       NaN                         NaN   
45541                       NaN                         NaN   
45542                       NaN                         NaN   
45543                       NaN                         NaN   

      assist_tackle_1_team assist_tackle_2_player_id  \
0                      NaN                       NaN   
1                      NaN                       NaN   
2                      NaN                       NaN   
3                      NaN                       NaN   
4                      NaN                       NaN   
...                    ...                       ...   
45535                  NaN                       NaN   
45538                  NaN                       NaN   
45541                  NaN                       NaN   
45542                  NaN                       NaN   
45543                  NaN                       NaN   

      assist_tackle_2_player_name assist_tackle_2_team  \
0                             NaN                  NaN   
1                             NaN                  NaN   
2                             NaN                  NaN   
3                             NaN                  NaN   
4                             NaN                  NaN   
...                           ...                  ...   
45535                         NaN                  NaN   
45538                         NaN                  NaN   
45541                         NaN                  NaN   
45542                         NaN                  NaN   
45543                         NaN                  NaN   

      assist_tackle_3_player_id assist_tackle_3_player_name  \
0                           NaN                         NaN   
1                           NaN                         NaN   
2                           NaN                         NaN   
3                           NaN                         NaN   
4                           NaN                         NaN   
...                         ...                         ...   
45535                       NaN                         NaN   
45538                       NaN                         NaN   
45541                       NaN                         NaN   
45542                       NaN                         NaN   
45543                       NaN                         NaN   

      assist_tackle_3_team assist_tackle_4_player_id  \
0                      NaN                       NaN   
1                      NaN            

In [14]:
new_df = df.copy()

new_df

Unnamed: 0   air_epa   air_wpa  air_yards  assist_tackle  \
0               1       NaN       NaN        NaN            0.0   
1               2       NaN       NaN        NaN            0.0   
2               3 -1.095212 -0.031647       -1.0            0.0   
3               4       NaN       NaN        NaN            0.0   
4               5       NaN       NaN        NaN            0.0   
...           ...       ...       ...        ...            ...   
45535       45536  4.335141  0.657133       12.0            0.0   
45538       45539  3.532878  0.610825       11.0            0.0   
45541       45542  2.888636  0.702366        5.0            0.0   
45542       45543  3.550080  0.899287        5.0            0.0   
45543       45544 -2.636491  0.010686        4.0            0.0   

      assist_tackle_1_player_id assist_tackle_1_player_name  \
0                           NaN                         NaN   
1                           NaN                         NaN   
2                           NaN                         NaN   
3                           NaN                         NaN   
4                           NaN                         NaN   
...                         ...                         ...   
45535                       NaN                         NaN   
45538                       NaN                         NaN   
45541                       NaN                         NaN   
45542                       NaN                         NaN   
45543                       NaN                         NaN   

      assist_tackle_1_team assist_tackle_2_player_id  \
0                      NaN                       NaN   
1                      NaN                       NaN   
2                      NaN                       NaN   
3                      NaN                       NaN   
4                      NaN                       NaN   
...                    ...                       ...   
45535                  NaN                       NaN   
45538                  NaN                       NaN   
45541                  NaN                       NaN   
45542                  NaN                       NaN   
45543                  NaN                       NaN   

      assist_tackle_2_player_name assist_tackle_2_team  \
0                             NaN                  NaN   
1                             NaN                  NaN   
2                             NaN                  NaN   
3                             NaN                  NaN   
4                             NaN                  NaN   
...                           ...                  ...   
45535                         NaN                  NaN   
45538                         NaN                  NaN   
45541                         NaN                  NaN   
45542                         NaN                  NaN   
45543                         NaN                  NaN   

      assist_tackle_3_player_id assist_tackle_3_player_name  \
0                           NaN                         NaN   
1                           NaN                         NaN   
2                           NaN                         NaN   
3                           NaN                         NaN   
4                           NaN                         NaN   
...                         ...                         ...   
45535                       NaN                         NaN   
45538                       NaN                         NaN   
45541                       NaN                         NaN   
45542                       NaN                         NaN   
45543                       NaN                         NaN   

      assist_tackle_3_team assist_tackle_4_player_id  \
0                      NaN                       NaN   
1                      NaN                       NaN   
2                      NaN                       NaN   
3                      NaN                       NaN   
4                      NaN            

#### 5.2 Identify Non Unique Player Names

In [7]:
# Create a data frame that contains the unique count of each player name under a given ID
# Filter on the IDs that correspond to more than one name

nunique_id = df[df.groupby(['play_maker_id'])['play_maker'].transform('nunique') > 1]['play_maker_id'].unique()


In [8]:
# Identify all the duplicate names

df[df['play_maker_id'].isin(nunique_id)]['play_maker'].unique()

array([], dtype=object)

In [9]:
# Create a dictionary of what the corrected names should be

name_corrections = {'D.Chark Jr.': 'D.Chark',
'Jos.Allen':'J.Allen',
'M.Ingram II': 'M.Ingram',
'A.Levine Sr.': 'A.Levine',
'R.Griffin III': 'R.Griffin',
'G.Minshew II':'G.Minshew',
'B.Snell Jr.':'B.Snell', 
'Tr.Edmunds':'T.Edmunds',
'R.James Jr.': 'R.James',
'J.Ross III':'J.Ross',
'W.Snead IV':'W.Snead', 
'M.Jones Jr.': 'M.Jones', 
'M.Sanu Sr.':'M.Sanu', 
'O.Beckham Jr.':'O.Beckham', 
'P.Dorsett II':'P.Dorsett'}

#### S5.3 Correct Name Uniqueness

In [10]:
# Create a function to correct the typos

def typo_correction(name):
    if name in name_corrections.keys():
        return name_corrections[name]
    else:
        return name

In [11]:
# apply the function to the dataframe

df['play_maker'] = df['play_maker'].apply(typo_correction)

#### S5.4 New Attempt

In [12]:
test = df[df['passer_player_id'].isin(nunique_id)].groupby(['passer_player_id','passer_player_name']).size().reset_index()

test.set_index('passer_player_id', inplace=True)

test


Empty DataFrame
Columns: [passer_player_name, 0]
Index: []

In [13]:

d = {player_id:(test.loc[player_id,'passer_player_name'][0],test.loc[player_id,'passer_player_name'][1]) for player_id in nunique_id}


In [14]:
test2 = df.copy()



In [15]:
test2.set_index('passer_player_id', inplace=True)


In [16]:
for dup in d.keys():
    test2.loc[dup,'passer_player_name'] = d[dup][0]

## 6. Relevant Plays

In [82]:
'''
Using a where statement use a binary indicator to Flag relevant plays 
such as passes, receptions, runs, field goals, extra points, and qb_kneels. 
'''

'\nUsing a where statement use a binary indicator to Flag relevant plays \nsuch as passes, receptions, runs, field goals, extra points, and qb_kneels. \n'

In [17]:
df['Flag'] = np.where((df['play_type'] == 'pass') | (df['play_type'] == 'run') | (df['play_type'] == 'field_goal') | (df['play_type'] == 'qb_kneel') | (df['play_type'] == 'extra_point') , 1, 0)


## 7. Extra Columns

In [18]:

df['Target'] = np.where(((df['play_type'] == 'pass') | (df['play_type'] == 'reception')) & (df['yards_after_catch'] != 'nan'), 1, 0)


df['reception'] = np.where(((df['play_type'] == 'pass') | (df['play_type'] == 'reception')) & (df['yards_after_catch'] >= 0), 1, 0)


/Users/royaharon/opt/anaconda3/lib/python3.7/site-packages/pandas/core/ops/__init__.py:1115: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  result = method(y)


In [19]:
df['play_type'] = np.where((df['play_type']=='no_play') & (df['interception']== 1), 'pass', df['play_type'])

## 8. Player Positions

In [19]:
'''
In this step positions will be assigned to each player based on the where their greatest number of yardage is focused
in. After their positions are set all the player data will be merged into one table that displays each players yard 
stats across rushing, passing, and receiving yards.
'''

'\nIn this step positions will be assigned to each player based on the where their greatest number of yardage is focused\nin. After their positions are set all the player data will be merged into one table that displays each players yard \nstats across rushing, passing, and receiving yards.\n'

In [20]:
df['playmaker_team'] = df['posteam']

pass_player_team = df[df.play_type == 'pass'][['play_maker', 'playmaker_team']]

pass_player_team = pass_player_team.drop_duplicates()

pass_play = df[df.play_type == 'pass'][['play_maker', 'yards_gained']]

pass_yards = pass_play.groupby('play_maker',as_index = False).yards_gained.sum()

pass_yards = pass_yards.rename(columns = {'yards_gained': 'pass_yards'})

pass_yards_final = pass_yards.merge(pass_player_team[["play_maker", "playmaker_team"]], on = 'play_maker', how = 'outer')

pass_yards_final


play_maker  pass_yards playmaker_team
0        A.Beck           6            DEN
1      A.Dalton        3247            CIN
2    A.Erickson          26            CIN
3      A.Kamara          13             NO
4         A.Lee          26            ARI
..          ...         ...            ...
106      T.Hill          46             NO
107   T.Siemian         -14            NYJ
108    T.Taylor          33            LAC
109     W.Grier         184            CAR
110    Z.Pascal           0            IND

[111 rows x 3 columns]

In [21]:
receiver_player_team = df[df.play_type == 'reception'][['play_maker', 'playmaker_team']]

receiver_player_team = receiver_player_team.drop_duplicates()

reception_play = df[df.play_type == 'reception'][['play_maker', 'yards_gained']]

reception_yards = reception_play.groupby('play_maker', as_index = False).yards_gained.sum()

reception_yards = reception_yards.rename(columns = {'yards_gained': 'reception_yards'})

reception_yards_final = reception_yards.merge(receiver_player_team[["play_maker", "playmaker_team"]], on = 'play_maker', how = 'outer')

reception_yards_final = reception_yards_final.dropna() 

reception_yards

play_maker  reception_yards
0    A.Abdullah              176
1       A.Armah               12
2     A.Auclair               22
3        A.Beck              180
4       A.Brown             2214
..          ...              ...
487    Z.Gentry                8
488     Z.Jones              432
489      Z.Line               72
490    Z.Pascal             1218
491    Z.Zenner               38

[492 rows x 2 columns]

In [22]:
rusher_player_team = df[df.play_type == 'run'][['play_maker', 'playmaker_team']]

rusher_player_team = rusher_player_team.drop_duplicates()

run_play = df[df.play_type == 'run'][['play_maker', 'yards_gained']]

run_yards = run_play.groupby('play_maker', as_index = False).yards_gained.sum()

run_yards = run_yards.rename(columns = {'yards_gained': 'run_yards'})

run_yards_final = run_yards.merge(rusher_player_team[["play_maker", "playmaker_team"]], on = 'play_maker', how = 'outer')

run_yards_final = run_yards_final.dropna() 

run_yards_final

play_maker  run_yards playmaker_team
0    A.Abdullah        115            MIN
1       A.Armah         11            CAR
2        A.Beck          3            DEN
3       A.Brown         65             NE
4       A.Brown         65            TEN
..          ...        ...            ...
336     Z.Jones          3            OAK
337      Z.Line         20             NO
338    Z.Pascal         16            IND
339    Z.Zenner         -2             NO
340    Z.Zenner         -2            ARI

[341 rows x 3 columns]

In [23]:
merged = pass_yards_final.merge(reception_yards_final[["play_maker", "reception_yards"]], on = 'play_maker', how = 'outer')
final_merged = merged.merge(run_yards_final[["play_maker", "run_yards"]], on = 'play_maker', how = 'outer')
final_merged['reception_yards'] = final_merged['reception_yards'].fillna(0)
final_merged['pass_yards'] = final_merged['pass_yards'].fillna(0)
final_merged['run_yards'] = final_merged['run_yards'].fillna(0)
final_merged['position'] = np.where((final_merged['pass_yards'] > final_merged['reception_yards']), 'QB', 'WR/TE')
final_merged['position'] = np.where((final_merged['run_yards'] > final_merged['pass_yards']) & (final_merged['run_yards'] > final_merged['reception_yards']) , 'RB', final_merged['position'])
# final_merged
final_merged[final_merged['play_maker'] == 'S.Sims']

play_maker  pass_yards playmaker_team  reception_yards  run_yards position
107     S.Sims         0.0            WAS            620.0       85.0    WR/TE

## 9. Stat Verification

In [ ]:
'''
In this step, the data that yardage data that had been calculated based on the plays in 2019 will be cross checked with
verified data to ensure that the data calculated in step 8 is the same as the verified data.
'''

In [47]:
# df_file_game = "../1. Additional-Data/2019 stats.xlsx"

xls = pd.ExcelFile("../1. Additional-Data/2019 stats.xlsx")

df_WR = pd.read_excel(xls, 'WR')

df_QB = pd.read_excel(xls, 'QB')

df_RB = pd.read_excel(xls, 'RB')


In [ ]:
"""
Reformats the names of the players so that the names in the
validated data file match those in the 2019 data excel sheet
"""

In [48]:
WR_ls1 = [wr[:wr.find('\\')] for wr in df_WR['Player']]
WR_final = []

for wr in WR_ls1:
    if '*' in wr:
        WR_final.append(wr[:wr.find('*')])
    else:
        WR_final.append(wr)

WR_final = [(col[0]+'.'+col[col.find(' '):]).replace(" ", "") for col in WR_final]

df_WR['Player'] = WR_final


In [26]:
RB_ls1 = [rb[:rb.find('\\')] for rb in df_RB['Player']]
RB_final = []

for rb in RB_ls1:
    if '*' in rb:
        RB_final.append(rb[:rb.find('*')])
    else:
        RB_final.append(rb)

RB_final = [(col[0]+'.'+col[col.find(' '):]).replace(" ", "") for col in RB_final]

df_RB['Player'] = RB_final

In [27]:
QB_ls1 = [qb[:qb.find('\\')] for qb in df_QB['Player']]
QB_final = []

for qb in QB_ls1:
    if '*' in qb:
        QB_final.append(qb[:qb.find('*')])
    else:
        QB_final.append(qb)
        

QB_final = [(col[0]+'.'+col[col.find(' '):]).replace(" ", "") for col in QB_final]

df_QB['Player'] = QB_final

### 9.1. QB validation

In [28]:
df_QB['Tm'] = np.where(df_QB['Tm'] == 'TAM', 'TB', df_QB['Tm'])
df_QB['Tm'] = np.where(df_QB['Tm'] == 'NOR', 'NO', df_QB['Tm'])
df_QB['Tm'] = np.where(df_QB['Tm'] == 'KAN', 'KC', df_QB['Tm'])
df_QB['Tm'] = np.where(df_QB['Tm'] == 'SFO', 'SF', df_QB['Tm'])
df_QB['Tm'] = np.where(df_QB['Tm'] == 'NWE', 'NE', df_QB['Tm'])
df_QB['Tm'] = np.where(df_QB['Tm'] == 'GNB', 'GB', df_QB['Tm'])
df_QB['Tm'] = np.where(df_QB['Tm'] == 'LAR', 'LA', df_QB['Tm'])

In [29]:

comp_list = df[(df['play_type'] == 'pass') & (df['reception'] == 1) & (df['sack'] != 1)].groupby(['play_maker', 'posteam'], as_index = False).play_maker_id.count()

Att_list = df[(df['play_type'] == 'pass') & (df['sack'] != 1)].groupby(['play_maker', 'posteam'], as_index = False).play_maker_id.count()

Att_comp = comp_list.merge(Att_list, on = ['play_maker', 'posteam'], how = 'inner')
Att_comp = Att_comp.rename(columns = {'posteam': 'player_team'})
Att_comp

play_maker player_team  play_maker_id_x  play_maker_id_y
0          A.Beck         DEN                1                1
1        A.Dalton         CIN              307              520
2      A.Erickson         CIN                1                1
3        A.Kamara          NO                1                1
4           A.Lee         ARI                1                1
..            ...         ...              ...              ...
89  T.Bridgewater          NO              132              195
90         T.Hill          NO                3                6
91      T.Siemian         NYJ                3                6
92       T.Taylor         LAC                4                6
93        W.Grier         CAR               28               52

[94 rows x 4 columns]

In [30]:
pd.set_option('display.max_rows',None)



A = df[(df['play_type'] == 'pass') & (df['sack'] != 1)].groupby(['play_maker', 'posteam'], as_index = False).agg({
    'yards_gained':['sum', 'max'],
    'pass_touchdown':['sum'],
    'interception':['sum']
    
})

A.columns = ['play_maker', 'player_team', 'Yards', 'Long', 'pass_touchdown', 'interceptions']

A.sort_values(['pass_touchdown'], ascending = False)

play_maker player_team  Yards  Long  pass_touchdown  interceptions
68          L.Jackson         BAL   3127    83            36.0            6.0
59          J.Winston          TB   5113    71            33.0           30.0
93           R.Wilson         SEA   4112    60            31.0            5.0
36         D.Prescott         DAL   4904    62            30.0           11.0
27            D.Brees          NO   2979    61            27.0            4.0
50        J.Garoppolo          SF   3982    75            27.0           13.0
24            C.Wentz         PHI   4041    53            27.0            7.0
63          K.Cousins         MIN   3605    66            26.0            6.0
83          P.Mahomes          KC   4033    83            26.0            5.0
37           D.Watson         HOU   3854    54            26.0           12.0
6           A.Rodgers          GB   4006    74            26.0            4.0
76             M.Ryan         ATL   4468    93            26.0           14.0
33            D.Jones         NYG   3031    75            24.0           12.0
100           T.Brady          NE   4059    59            24.0            8.0
84           P.Rivers         LAC   4617    84            23.0           20.0
14         B.Mayfield         CLE   3827    89            22.0           21.0
92        R.Tannehill         TEN   2742    91            22.0            6.0
51             J.Goff          LA   4638    66            22.0           16.0
28             D.Carr         OAK   4054    75            21.0            8.0
88      R.Fitzpatrick         MIA   3531    51            20.0           13.0
65           K.Murray         ARI   3728    88            20.0           12.0
78         M.Stafford         DET   2499    66            19.0            5.0
94          S.Darnold         NYJ   3030    92            19.0           13.0
44         J.Brissett         IND   2944    50            18.0            6.0
79         M.Trubisky         CHI   3140    53            17.0           10.0
61            K.Allen         CAR   3322    52            17.0           16.0
1            A.Dalton         CIN   3496    66            16.0           14.0
43            J.Allen         BUF   2411    53            16.0            9.0
75          M.Rudolph         PIT   1765    76            13.0            9.0
42       G.Minshew II         JAX   1835    70            12.0            4.0
18           C.Keenum         WAS   1707    69            11.0            5.0
41          G.Minshew         JAX   1442    69             9.0            2.0
101     T.Bridgewater          NO   1384    45             9.0            2.0
30          D.Haskins         WAS   1367    75             7.0            7.0
34             D.Lock         DEN   1020    48             7.0            3.0
72          M.Mariota         TEN   1203    75             7.0            2.0
49           J.Flacco         DEN   1824    70             6.0            5.0
38          E.Manning         NYG   1042    55             6.0            5.0
31           D.Hodges         PIT   1063    79             5.0            8.0
46          J.Driskel         DET    685    47             4.0            4.0
60          Jos.Allen         BUF    682    49             4.0            0.0
73            M.Moore          KC    659    57             4.0            0.0
26           D.Blough         DET    984    75             4.0            6.0
11            B.Hoyer         IND    372    23             4.0            4.0
81            N.Foles         JAX    738    39             3.0            2.0
77           M.Schaub         ATL    582    35             3.0            1.0
9             B.Allen         DEN    515    75             3.0            2.0
17           C.Daniel         CHI    435    37             3.0            2.0
87           R.Finley         CIN    474    47             2.0            2.0
71            M.Haack         MIA      1     1             1.0            0.0
70          M.Glennon         OAK

In [31]:
Final_QB_Stats = A.merge(Att_comp, on = ['play_maker', 'player_team'], how = 'inner')
Final_QB_Stats = Final_QB_Stats.rename(columns = {'play_maker_id_x': 'completions'})
Final_QB_Stats = Final_QB_Stats.rename(columns = {'play_maker_id_y': 'attempts'})


Final_QB_Stats

play_maker player_team  Yards  Long  pass_touchdown  interceptions  \
0             A.Beck         DEN      6     6             0.0            0.0   
1           A.Dalton         CIN   3496    66            16.0           14.0   
2         A.Erickson         CIN     26    26             0.0            0.0   
3           A.Kamara          NO     13    13             0.0            0.0   
4              A.Lee         ARI     26    26             0.0            0.0   
5         A.McCarron         HOU    225    21             0.0            1.0   
6          A.Rodgers          GB   4006    74            26.0            4.0   
7           A.Tanney         NYG      1     1             0.0            0.0   
8           A.Wilson         MIA     20    20             0.0            0.0   
9            B.Allen         DEN    515    75             3.0            2.0   
10         B.Bortles          LA      3     3             0.0            0.0   
11           B.Hoyer         IND    372    23             4.0            4.0   
12         B.Hundley         ARI     49    28             0.0            0.0   
13            B.Kern         TEN     11    11             0.0            0.0   
14        B.Mayfield         CLE   3827    89            22.0           21.0   
15  B.Roethlisberger         PIT    351    45             0.0            1.0   
16          C.Daniel         CHI    435    37             3.0            2.0   
17          C.Keenum         WAS   1707    69            11.0            5.0   
18           C.McCoy         WAS    122    22             0.0            1.0   
19          C.Newton         CAR    572    44             0.0            1.0   
20          C.Sutton         DEN     38    38             0.0            0.0   
21           C.Wentz         PHI   4041    53            27.0            7.0   
22        D.Amendola         DET     19    19             1.0            0.0   
23          D.Blough         DET    984    75             4.0            6.0   
24           D.Brees          NO   2979    61            27.0            4.0   
25            D.Carr         OAK   4054    75            21.0            8.0   
26         D.Haskins         WAS   1367    75             7.0            7.0   
27          D.Hodges         PIT   1063    79             5.0            8.0   
28         D.Hopkins         HOU      6     6             1.0            1.0   
29           D.Jones         NYG   3031    75            24.0           12.0   
30            D.Lock         DEN   1020    48             7.0            3.0   
31          D.Pettis          SF     16    16             0.0            0.0   
32        D.Prescott         DAL   4904    62            30.0           11.0   
33          D.Watson         HOU   3854    54            26.0           12.0   
34         E.Manning         NYG   1042    55             6.0            5.0   
35         E.Sanders          SF     35    35             1.0            0.0   
36         G.Minshew         JAX   1442    69             9.0            2.0   
37      G.Minshew II         JAX   1835    70            12.0            4.0   
38           J.Allen         BUF   2411    53            16.0            9.0   
39        J.Brissett         IND   2944    50            18.0            6.0   
40           J.Brown         BUF     28    28             1.0            0.0   
41         J.Driskel         DET    685    47             4.0            4.0   
42         J.Edelman          NE     47    32             1.0            0.0   
43          J.Flacco         DEN   1824    70             6.0            5.0   
44       J.Garoppolo          SF   3982    75            27.0           13.0   
45            J.Goff          LA   4638    66            22.0           16.0   
46          J.Hekker          LA     28    23             0.0            1.0   
47          J.McCown         PHI     24    13             0.0            0.0   
48           J.Rosen         MIA    567    40             1.0            5.0   
49        

In [32]:
df_QB = df_QB.rename(columns = {'Player': 'play_maker'})
df_QB = df_QB.rename(columns = {'Tm': 'player_team'})
df_QB 
valid_table_QB = Final_QB_Stats[['play_maker', 'player_team', 'Yards', 'pass_touchdown', 
                                'interceptions', 'completions', 'attempts']].merge(df_QB[['play_maker', 'player_team', 'Yds', 'TD', 'Int', 'Cmp', 'Att']], on = ['play_maker', 'player_team'], how = 'left')

valid_table_QB['delta_yds'] = valid_table_QB['Yards'] - valid_table_QB['Yds']
valid_table_QB['delta_TD'] = valid_table_QB['pass_touchdown'] - valid_table_QB['TD']
valid_table_QB['delta_int'] = valid_table_QB['interceptions'] - valid_table_QB['Int']
valid_table_QB['delta_cmp'] = valid_table_QB['completions'] - valid_table_QB['Cmp']
valid_table_QB['delta_att'] = valid_table_QB['attempts'] - valid_table_QB['Att']
valid_table_QB.sort_values(['Yards'], ascending = False)


play_maker player_team  Yards  pass_touchdown  interceptions  \
52         J.Winston          TB   5113            33.0           30.0   
32        D.Prescott         DAL   4904            30.0           11.0   
45            J.Goff          LA   4638            22.0           16.0   
76          P.Rivers         LAC   4617            23.0           20.0   
69            M.Ryan         ATL   4468            26.0           14.0   
83          R.Wilson         SEA   4112            31.0            5.0   
88           T.Brady          NE   4059            24.0            8.0   
25            D.Carr         OAK   4054            21.0            8.0   
21           C.Wentz         PHI   4041            27.0            7.0   
75         P.Mahomes          KC   4033            26.0            5.0   
6          A.Rodgers          GB   4006            26.0            4.0   
44       J.Garoppolo          SF   3982            27.0           13.0   
33          D.Watson         HOU   3854            26.0           12.0   
14        B.Mayfield         CLE   3827            22.0           21.0   
58          K.Murray         ARI   3728            20.0           12.0   
56         K.Cousins         MIN   3605            26.0            6.0   
78     R.Fitzpatrick         MIA   3531            20.0           13.0   
1           A.Dalton         CIN   3496            16.0           14.0   
54           K.Allen         CAR   3322            17.0           16.0   
72        M.Trubisky         CHI   3140            17.0           10.0   
61         L.Jackson         BAL   3127            36.0            6.0   
29           D.Jones         NYG   3031            24.0           12.0   
84         S.Darnold         NYJ   3030            19.0           13.0   
24           D.Brees          NO   2979            27.0            4.0   
39        J.Brissett         IND   2944            18.0            6.0   
82       R.Tannehill         TEN   2742            22.0            6.0   
71        M.Stafford         DET   2499            19.0            5.0   
38           J.Allen         BUF   2411            16.0            9.0   
37      G.Minshew II         JAX   1835            12.0            4.0   
43          J.Flacco         DEN   1824             6.0            5.0   
68         M.Rudolph         PIT   1765            13.0            9.0   
17          C.Keenum         WAS   1707            11.0            5.0   
36         G.Minshew         JAX   1442             9.0            2.0   
89     T.Bridgewater          NO   1384             9.0            2.0   
26         D.Haskins         WAS   1367             7.0            7.0   
65         M.Mariota         TEN   1203             7.0            2.0   
27          D.Hodges         PIT   1063             5.0            8.0   
34         E.Manning         NYG   1042             6.0            5.0   
30            D.Lock         DEN   1020             7.0            3.0   
23          D.Blough         DET    984             4.0            6.0   
73           N.Foles         JAX    738             3.0            2.0   
41         J.Driskel         DET    685             4.0            4.0   
53         Jos.Allen         BUF    682             4.0            0.0   
66           M.Moore          KC    659             4.0            0.0   
70          M.Schaub         ATL    582             3.0            1.0   
19          C.Newton         CAR    572             0.0            1.0   
48           J.Rosen         MIA    567             1.0            5.0   
9            B.Allen         DEN    515             3.0            2.0   
77          R.Finley         CIN    474             2.0            2.0   
16          C.Daniel         CHI    435             3.0            2.0   
60            L.Falk         NYJ    416             0.0            3.0   
11           B.Hoyer         IND    372             4.0            4.0   
62         M.Barkley         BUF    359             0.0            3.0   
15  B.Roethlis

### 9.2. RB Validation Table

In [ ]:
"""
RB validated stat table is formulated
"""

In [33]:

df_RB['Tm'] = np.where(df_RB['Tm'] == 'TAM', 'TB', df_RB['Tm'])
df_RB['Tm'] = np.where(df_RB['Tm'] == 'NOR', 'NO', df_RB['Tm'])
df_RB['Tm'] = np.where(df_RB['Tm'] == 'KAN', 'KC', df_RB['Tm'])
df_RB['Tm'] = np.where(df_RB['Tm'] == 'SFO', 'SF', df_RB['Tm'])
df_RB['Tm'] = np.where(df_RB['Tm'] == 'NWE', 'NE', df_RB['Tm'])
df_RB['Tm'] = np.where(df_RB['Tm'] == 'GNB', 'GB', df_RB['Tm'])
df_RB['Tm'] = np.where(df_RB['Tm'] == 'LAR', 'LA', df_RB['Tm'])


In [34]:
pd.set_option('display.max_rows',None)

RB_stats = df[df['play_type'] == 'run'].groupby(['play_maker', 'posteam'], as_index = False).agg({
    'yards_gained':['sum', 'max'],
    'rush_touchdown':['sum'],
    
})


RB_stats.columns = ['play_maker', 'player_team', 'Yards', 'Long', 'rush_touchdown']
RB_stats[RB_stats['play_maker'] == 'D.Johnson']

play_maker player_team  Yards  Long  rush_touchdown
89  D.Johnson         ARI    345    18             2.0
90  D.Johnson         CLE     21    13             0.0
91  D.Johnson         HOU    410    40             2.0
92  D.Johnson         PIT     41    17             0.0

In [35]:
fums = df.groupby(['play_maker', 'posteam'], as_index = False).agg({
    'fumble':['sum']
    
})
fums = fums.rename(columns = {'posteam': 'player_team'})

valid_RB_stats = RB_stats.merge(fums, on = ['play_maker', 'player_team'], how = 'outer')
valid_RB_stats = valid_RB_stats.rename(columns = {('fumble', 'sum'): 'fumble'})
valid_RB_stats

# fums[fums['play_maker'] == 'D.Johnson']


/Users/royaharon/opt/anaconda3/lib/python3.7/site-packages/pandas/core/reshape/merge.py:617: UserWarning: merging between different levels can give an unintended result (1 levels on the left, 2 on the right)
  warnings.warn(msg, UserWarning)
/Users/royaharon/opt/anaconda3/lib/python3.7/site-packages/pandas/core/generic.py:3946: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_axis = axis.drop(labels, errors=errors)


play_maker player_team   Yards  Long  rush_touchdown  fumble
0            A.Abdullah         MIN   115.0  15.0             0.0     0.0
1               A.Armah         CAR    11.0   4.0             1.0     0.0
2                A.Beck         DEN     3.0   3.0             0.0     0.0
3               A.Brown          NE     5.0   5.0             0.0     0.0
4               A.Brown         TEN    60.0  49.0             1.0     2.0
5              A.Cooper         DAL     6.0   6.0             0.0     0.0
6              A.Dalton         CIN    87.0  17.0             4.0    14.0
7              A.Ekeler         LAC   557.0  35.0             3.0     5.0
8            A.Erickson         CIN    33.0  17.0             0.0     2.0
9           A.Humphries         TEN     1.0   1.0             0.0     0.0
10             A.Ingold         OAK    17.0   4.0             0.0     0.0
11           A.Isabella         ARI    15.0   6.0             0.0     0.0
12           A.Janovich         DEN     1.0   1.0             1.0     0.0
13            A.Jeffery         PHI     2.0   2.0             1.0     0.0
14              A.Jones          GB  1084.0  56.0            16.0     4.0
15             A.Kamara          NO   797.0  40.0             5.0     5.0
16             A.Lazard          GB    21.0  21.0             0.0     0.0
17             A.Levine         BAL    60.0  60.0             0.0     0.0
18         A.Levine Sr.         BAL     2.0   2.0             0.0     0.0
19           A.Mattison         MIN   462.0  35.0             1.0     1.0
20           A.McCarron         HOU    39.0  18.0             1.0     0.0
21             A.Miller         CHI    -1.0  -1.0             0.0     1.0
22             A.Morris         ARI     4.0   4.0             0.0     0.0
23           A.Peterson         WAS   898.0  32.0             5.0     4.0
24            A.Roberts         BUF     7.0   7.0             0.0     0.0
25           A.Robinson         CHI     2.0   2.0             0.0     0.0
26            A.Rodgers          GB   204.0  17.0             1.0    10.0
27            A.Sherman          KC     9.0   5.0             0.0     0.0
28            A.Thielen         MIN     6.0   3.0             1.0     2.0
29             A.Wilson         MIA    45.0  28.0             0.0     0.0
30              B.Allen         DEN    42.0  11.0             0.0     1.0
31              B.Anger         HOU    -5.0  -5.0             0.0     0.0
32             B.Bolden          NE    68.0  21.0             3.0     0.0
33            B.Bortles          LA    -9.0   1.0             0.0     0.0
34              B.Cooks          LA    52.0  27.0             0.0     0.0
35             B.Fowler         NYG    20.0  20.0             0.0     0.0
36               B.Hill         ATL   323.0  27.0             2.0     0.0
37              B.Hoyer         IND     7.0   6.0             0.0     2.0
38            B.Hundley         ARI    44.0  14.0             0.0     0.0
39               B.Kern         TEN     0.0   0.0             0.0     0.0
40           B.Mayfield         CLE   144.0  18.0             3.0     8.0
41           B.Perriman          TB    16.0  13.0             0.0     0.0
42             B.Powell         NYJ   229.0  17.0             0.0     0.0
43     B.Roethlisberger         PIT     7.0   7.0             0.0     2.0
44         B.Scarbrough         DET   377.0  30.0             1.0     1.0
45              B.Scott         PHI   245.0  25.0             5.0     3.0
46              B.Snell         PIT   118.0  23.0             0.0     0.0
47          B.Snell Jr.         PIT   308.0  21.0             2.0     1.0
48           C.Anderson         DET    43.0   9.0             0.0     0.0
49             C.Carson         SEA  1230.0  59.0             7.0     8.0
50             C.Daniel         CHI     6.0   4.0             0.0     0.0
51            C.Edmonds         ARI   303.0  37.0             4.0     0.0
52             C.Godwin          TB     8.0   8.0             0.0     0.0
53               

In [38]:
df_RB = df_RB.rename(columns = {'Player': 'play_maker'})

df_RB = df_RB.rename(columns = {'Tm': 'player_team'})

valid_table_RB = valid_RB_stats.merge(df_RB[['play_maker', 'player_team', 'Yds', 'Lng', 'TD', 'Fmb']], on = ['play_maker', 'player_team'], how = 'outer')

valid_table_RB[valid_table_RB['play_maker'] == 'D.Johnson']

play_maker player_team  Yards  Long  rush_touchdown  fumble    Yds   Lng  \
89  D.Johnson         ARI  345.0  18.0             2.0     2.0  345.0  18.0   
90  D.Johnson         CLE   21.0  13.0             0.0     0.0   21.0  13.0   
91  D.Johnson         HOU  410.0  40.0             2.0     1.0  410.0  40.0   
92  D.Johnson         PIT   41.0  17.0             0.0     6.0   41.0  17.0   

     TD  Fmb  
89  2.0  1.0  
90  0.0  0.0  
91  2.0  1.0  
92  0.0  5.0

In [39]:

valid_table_RB['delta_yds'] = valid_table_RB['Yards'] - valid_table_RB['Yds']
valid_table_RB['delta_Lng'] = valid_table_RB['Long'] - valid_table_RB['Lng']
valid_table_RB['delta_TD'] = valid_table_RB['rush_touchdown'] - valid_table_RB['TD']
valid_table_RB['delta_Fmb'] = valid_table_RB['fumble'] - valid_table_RB['Fmb']
valid_table_RB.sort_values(['Yards'], ascending = False)

play_maker player_team   Yards  Long  rush_touchdown  fumble  \
85              D.Henry         TEN  1540.0  74.0            16.0     5.0   
244             N.Chubb         CLE  1494.0  88.0             8.0     4.0   
59          C.McCaffrey         CAR  1389.0  84.0            15.0     1.0   
124           E.Elliott         DAL  1357.0  33.0            12.0     3.0   
49             C.Carson         SEA  1230.0  59.0             7.0     8.0   
208           L.Jackson         BAL  1226.0  47.0             7.0    10.0   
207         L.Fournette         JAX  1152.0  81.0             3.0     2.0   
167            J.Jacobs         OAK  1150.0  51.0             7.0     1.0   
172             J.Mixon         CIN  1137.0  41.0             5.0     0.0   
77               D.Cook         MIN  1135.0  75.0            13.0     5.0   
229              M.Mack         IND  1093.0  63.0             8.0     0.0   
14              A.Jones          GB  1084.0  56.0            16.0     4.0   
54               C.Hyde         HOU  1070.0  58.0             6.0     4.0   
258           P.Lindsay         DEN  1011.0  40.0             7.0     0.0   
285           S.Barkley         NYG  1003.0  68.0             6.0     2.0   
289            S.Michel          NE   912.0  26.0             7.0     2.0   
23           A.Peterson         WAS   898.0  32.0             5.0     4.0   
97         D.Montgomery         CHI   889.0  55.0             6.0     2.0   
311            T.Gurley          LA   859.0  25.0            12.0     3.0   
234           M.Sanders         PHI   818.0  65.0             3.0     3.0   
15             A.Kamara          NO   797.0  40.0             5.0     5.0   
206              L.Bell         NYJ   789.0  19.0             3.0     2.0   
105        D.Singletary         BUF   775.0  38.0             2.0     4.0   
278           R.Mostert          SF   772.0  41.0             8.0     1.0   
277             R.Jones          TB   724.0  49.0             6.0     4.0   
132           G.Edwards         BAL   711.0  63.0             2.0     2.0   
79            D.Freeman         ATL   656.0  28.0             2.0     4.0   
196             K.Drake         ARI   643.0  80.0             8.0     0.0   
210            L.Murray          NO   637.0  30.0             5.0     0.0   
213            M.Breida          SF   623.0  83.0             1.0     2.0   
220            M.Gordon         LAC   612.0  24.0             8.0     5.0   
129              F.Gore         BUF   599.0  41.0             2.0     0.0   
224            M.Ingram         BAL   587.0  53.0             7.0     3.0   
202            K.Murray         ARI   558.0  35.0             4.0     9.0   
7              A.Ekeler         LAC   557.0  35.0             3.0     5.0   
305           T.Coleman          SF   544.0  48.0             6.0     0.0   
165            J.Howard         PHI   525.0  20.0             6.0     0.0   
123        Dam.Williams          KC   498.0  91.0             5.0     1.0   
272           R.Freeman         DEN   496.0  26.0             3.0     0.0   
252            P.Barber          TB   470.0  17.0             6.0     1.0   
209             L.McCoy          KC   465.0  39.0             4.0     4.0   
150            J.Conner         PIT   464.0  25.0             4.0     2.0   
19           A.Mattison         MIN   462.0  35.0             1.0     1.0   
182          J.Williams          GB   460.0  45.0             1.0     0.0   
322           T.Pollard         DAL   457.0  44.0             2.0     1.0   
225         M.Ingram II         BAL   435.0  29.0             3.0     1.0   
145             J.Allen         BUF   425.0  18.0             5.0    11.0   
116            D.Watson         HOU   424.0  30.0             7.0    13.0   
91            D.Johnson         HOU   410.0  40.0             2.0     1.0   
200           K.Johnson         DET   403.0  20.0             3.0     1.0   
115        D.Washington         OAK   387.0  36.0             3.0     0.0   
44       

### 9.3. WR Validation Table

In [125]:
"""
WR_stats
"""

'\nWR_stats\n'

In [49]:
df_WR['Tm'] = np.where(df_WR['Tm'] == 'TAM', 'TB', df_WR['Tm'])
df_WR['Tm'] = np.where(df_WR['Tm'] == 'NOR', 'NO', df_WR['Tm'])
df_WR['Tm'] = np.where(df_WR['Tm'] == 'KAN', 'KC', df_WR['Tm'])
df_WR['Tm'] = np.where(df_WR['Tm'] == 'SFO', 'SF', df_WR['Tm'])
df_WR['Tm'] = np.where(df_WR['Tm'] == 'NWE', 'NE', df_WR['Tm'])
df_WR['Tm'] = np.where(df_WR['Tm'] == 'GNB', 'GB', df_WR['Tm'])
df_WR['Tm'] = np.where(df_WR['Tm'] == 'LAR', 'LA', df_WR['Tm'])

In [50]:
pd.set_option('display.max_rows',None)

WR_stats = df[df['play_type'] == 'reception'].groupby(['play_maker', 'posteam'], as_index = False).agg({
    'yards_gained':['sum', 'max'],
    'pass_touchdown':['sum'],
    'fumble':['sum'],
    'reception':['sum'],
    'Target':['sum']
    
})

WR_stats.columns = ['play_maker', 'player_team', 'Yards', 'Long', 'receiving_touchdown', 'fumble', 'reception', 'target']
WR_stats

play_maker player_team  Yards  Long  receiving_touchdown  fumble  \
0            A.Abdullah         MIN    176    16                  2.0     0.0   
1               A.Armah         CAR     12     4                  0.0     0.0   
2             A.Auclair          TB     22    11                  0.0     0.0   
3                A.Beck         DEN    180    29                  2.0     0.0   
4               A.Brown          NE    112    20                  2.0     0.0   
5               A.Brown         TEN   2102    91                 16.0     2.0   
6            A.Callaway         CLE    178    41                  0.0     0.0   
7                A.Carr          NO     18     9                  0.0     0.0   
8              A.Cooper         DAL   2378    53                 16.0     0.0   
9              A.Dalton         CIN     -8    -4                  0.0     0.0   
10              A.Dulin         IND     34    13                  0.0     0.0   
11             A.Ekeler         LAC   1986    84                 16.0     4.0   
12           A.Erickson         CIN   1058    52                  0.0     2.0   
13            A.Firkser         TEN    408    39                  2.0     0.0   
14            A.Hollins         MIN     92    35                  0.0     0.0   
15             A.Hooper         ATL   1578    35                 12.0     0.0   
16          A.Humphries         TEN    748    30                  4.0     0.0   
17              A.Hurns         MIA    832    27                  4.0     2.0   
18             A.Ingold         OAK     88    14                  2.0     0.0   
19           A.Isabella         ARI    378    88                  2.0     0.0   
20           A.Janovich         DEN     84    22                  0.0     0.0   
21            A.Jeffery         PHI    980    38                  8.0     0.0   
22              A.Jones          GB    948    67                  6.0     2.0   
23             A.Kamara          NO   1066    41                  2.0     2.0   
24             A.Lazard          GB    954    43                  6.0     0.0   
25           A.Mattison         MIN    164    17                  0.0     0.0   
26             A.Miller         CHI   1312    35                  4.0     0.0   
27             A.Patton         LAC    112    15                  0.0     0.0   
28           A.Peterson         WAS    284    22                  0.0     2.0   
29            A.Roberts         BUF     40     7                  0.0     0.0   
30           A.Robinson         CHI   2294    49                 14.0     0.0   
31            A.Shaheen         CHI    152    18                  0.0     0.0   
32            A.Sherman          KC     44    15                  0.0     0.0   
33               A.Tate         CIN   1150    33                  2.0     2.0   
34            A.Thielen         MIN    844    44                 12.0     2.0   
35             A.Wilson         MIA    702    35                  2.0     0.0   
36               B.Bell          KC    134    30                  0.0     0.0   
37            B.Berrios         NYJ    230    69                  0.0     0.0   
38             B.Bolden          NE    222    29                  2.0     0.0   
39         B.Braunecker         CHI    118    18                  2.0     0.0   
40              B.Cooks          LA   1166    57                  4.0     0.0   
41             B.Fowler         NYG    390    17                  0.0     0.0   
42               B.Hill         ATL    138    12                  2.0     0.0   
43             B.Jarwin         DAL    730    42                  6.0     2.0   
44             B.Koyack         JAX     18     9                  0.0     0.0   
45           B.Perriman          TB   1290    44                 12.0     0.0   
46             B.Powell         NYJ     66     9                  0.0     0.0   
47            B.Pringle          KC    340    28                  2.0     0.0   
48         B.Scarbrough         DET     10  

In [51]:
df_WR = df_WR.rename(columns = {'Player': 'play_maker'})
df_WR = df_WR.rename(columns = {'Tm': 'player_team'})

valid_table_WR = WR_stats.merge(df_WR, on = ['play_maker', 'player_team'], how = 'outer')
valid_table_WR.sort_values(['Yds'], ascending = False)
valid_table_WR['delta_yds'] = valid_table_WR['Yards'] - valid_table_WR['Yds']
valid_table_WR['delta_rec'] = valid_table_WR['reception'] - valid_table_WR['Rec']
valid_table_WR['delta_Tgt'] = valid_table_WR['target'] - valid_table_WR['Tgt']
valid_table_WR['delta_TD'] = valid_table_WR['receiving_touchdown'] - valid_table_WR['TD']
valid_table_WR[['play_maker', 'receiving_touchdown', 'TD', 'Yards', 'Yds','reception', 'Rec', 'target', 'Tgt', 'delta_TD', 'delta_yds', 'delta_rec', 'delta_Tgt']].sort_values(['Yds'], ascending = False)













play_maker  receiving_touchdown    TD   Yards     Yds  reception  \
372            M.Thomas                 18.0   9.0  3450.0  1725.0      298.0   
256             J.Jones                 12.0   6.0  2788.0  1394.0      196.0   
67             C.Godwin                 18.0   9.0  2670.0  1333.0      172.0   
489             T.Kelce                 10.0   5.0  2504.0  1229.0      186.0   
150            D.Parker                 18.0   9.0  2404.0  1202.0      144.0   
295             K.Allen                 12.0   6.0  2398.0  1199.0      202.0   
307          K.Golladay                 22.0  11.0  2380.0  1190.0      130.0   
8              A.Cooper                 16.0   8.0  2378.0  1189.0      156.0   
145             D.Moore                  8.0   4.0  2350.0  1175.0      172.0   
258            J.Landry                 12.0   6.0  2348.0  1174.0      162.0   
129           D.Hopkins                 14.0   7.0  2334.0  1165.0      200.0   
76               C.Kupp                 20.0  10.0  2322.0  1161.0      186.0   
347             M.Evans                 16.0   8.0  2318.0  1157.0      132.0   
30           A.Robinson                 14.0   7.0  2294.0  1147.0      192.0   
170            D.Waller                  6.0   3.0  2290.0  1145.0      180.0   
442             R.Woods                  4.0   2.0  2268.0  1134.0      178.0   
448             S.Diggs                 12.0   6.0  2252.0  1130.0      118.0   
235           J.Edelman                 12.0   6.0  2238.0  1117.0      192.0   
89             C.Sutton                 12.0   6.0  2224.0  1112.0      140.0   
348            M.Gallup                 12.0   6.0  2214.0  1107.0      132.0   
228             J.Brown                 12.0   6.0  2120.0  1060.0      142.0   
491           T.Lockett                 16.0   8.0  2114.0  1057.0      164.0   
204            G.Kittle                 10.0   5.0  2106.0  1053.0      170.0   
5               A.Brown                 16.0   8.0  2102.0  1051.0       98.0   
462              T.Boyd                 10.0   5.0  2092.0  1046.0      174.0   
534        O.BeckhamJr.                  NaN   4.0     NaN  1035.0        NaN   
110             D.Chark                 10.0   8.0  1056.0  1008.0       58.0   
80          C.McCaffrey                  8.0   4.0  2010.0  1005.0      232.0   
378          M.Williams                  4.0   2.0  2002.0  1001.0       94.0   
97              D.Adams                 10.0   5.0  1998.0   997.0      160.0   
11             A.Ekeler                 16.0   8.0  1986.0   993.0      184.0   
493          T.McLaurin                 14.0   7.0  1838.0   919.0      114.0   
526              Z.Ertz                 12.0   6.0  1836.0   916.0      174.0   
537           D.Metcalf                  NaN   7.0     NaN   900.0        NaN   
535           E.Sanders                  NaN   5.0     NaN   869.0        NaN   
85             C.Ridley                 14.0   7.0  1736.0   866.0      118.0   
479              T.Hill                 14.0   7.0  1720.0   860.0      108.0   
336           M.Andrews                 20.0  10.0  1704.0   852.0      126.0   
232           J.Crowder                 12.0   6.0  1666.0   833.0      156.0   
415              R.Cobb                  6.0   3.0  1656.0   828.0      108.0   
323        L.Fitzgerald                  8.0   4.0  1608.0   804.0      148.0   
156            D.Samuel                  6.0   3.0  1608.0   802.0      114.0   
15             A.Hooper                 12.0   6.0  1578.0   787.0      150.0   
360             M.Jones                 16.0   9.0  1310.0   779.0       98.0   
538          R.Anderson                  NaN   5.0     NaN   779.0        NaN   
55            C.Beasley                 12.0   6.0  1564.0   778.0      134.0   
63             C.Conley                 10.0   5.0  1554.0   775.0       92.0   
161           D.Slayton                 16.0   8.0  1492.0   740.0       94.0   
284        J.Washington                  6.0

## Zone Label

Unnamed: 0  play_id     game_id home_team away_team posteam  \
0               1       35  2019090500       CHI        GB      GB   
1               2       50  2019090500       CHI        GB      GB   
2               3       71  2019090500       CHI        GB      GB   
3               4       95  2019090500       CHI        GB      GB   
4               5      125  2019090500       CHI        GB      GB   
...           ...      ...         ...       ...       ...     ...   
45541       45542     3955  2019122915       SEA        SF     SEA   
45542       45543     3977  2019122915       SEA        SF     SEA   
45543       45544     3999  2019122915       SEA        SF     SEA   
45544       45545     4080  2019122915       SEA        SF      SF   
45545       45546     4101  2019122915       SEA        SF     NaN   

      posteam_type defteam side_of_field  yardline_100   game_date  \
0             away     CHI           CHI          35.0  2019-09-05   
1             away     CHI            GB          75.0  2019-09-05   
2             away     CHI            GB          75.0  2019-09-05   
3             away     CHI            GB          75.0  2019-09-05   
4             away     CHI            GB          85.0  2019-09-05   
...            ...     ...           ...           ...         ...   
45541         home      SF            SF           5.0  2019-12-29   
45542         home      SF            SF           5.0  2019-12-29   
45543         home      SF            SF           5.0  2019-12-29   
45544         away     SEA            SF          99.0  2019-12-29   
45545          NaN     NaN            SF           NaN  2019-12-29   

       quarter_seconds_remaining  half_seconds_remaining  \
0                          900.0                  1800.0   
1                          900.0                  1800.0   
2                          873.0                  1773.0   
3                          825.0                  1725.0   
4                          795.0                  1695.0   
...                          ...                     ...   
45541                       22.0                    22.0   
45542                       15.0                    15.0   
45543                       12.0                    12.0   
45544                        9.0                     9.0   
45545                        0.0                     0.0   

       game_seconds_remaining game_half  quarter_end  drive  sp  qtr  down  \
0                      3600.0     Half1            0      1   0    1   NaN   
1                      3600.0     Half1            0      1   0    1   1.0   
2                      3573.0     Half1            0      1   0    1   2.0   
3                      3525.0     Half1            0      1   0    1   3.0   
4                      3495.0     Half1            0      1   0    1   4.0   
...                       ...       ...          ...    ...  ..  ...   ...   
45541                    22.0     Half2            0     16   0    4   2.0   
45542                    15.0     Half2            0     16   0    4   3.0   
45543                    12.0     Half2            0     16   0    4   4.0   
45544                     9.0     Half2            0     17   0    4   1.0   
45545                     0.0     Half2            1     17   0    4   NaN   

       goal_to_go   time   yrdln  ydstogo  ydsnet  \
0             0.0  15:00  CHI 35        0     -10   
1             0.0  15:00   GB 25       10     -10   
2             0.0  14:33   GB 25       10     -10   
3             0.0  13:45   GB 25       10     -10   
4             0.0  13:15   GB 15       20     -10   
...           ...    ...     ...      ...     ...   
45541         1.0  00:22    SF 5        5      72   
45542         1.0  00:15    SF 5        5      72   
45543         1.0  00:12    SF 5        5      72   
45544         0.0  00:09    SF 1       10       2   
45545         NaN  00:00    SF 1        0       2   

                              

In [12]:
df['Zone'] = np.where(df['yardline_100'] <= 5, 'Inside the 5', np.NaN)
df['Zone'] = np.where((df['yardline_100'] > 5) & (df['yardline_100'] <= 20) , 'Red Zone', df['Zone'])
df['Zone'] = np.where(df['yardline_100'] > 20 , 'Other', df['Zone'])

df

Unnamed: 0  play_id     game_id home_team away_team posteam  \
0               1       35  2019090500       CHI        GB      GB   
1               2       50  2019090500       CHI        GB      GB   
2               3       71  2019090500       CHI        GB      GB   
3               4       95  2019090500       CHI        GB      GB   
4               5      125  2019090500       CHI        GB      GB   
...           ...      ...         ...       ...       ...     ...   
45541       45542     3955  2019122915       SEA        SF     SEA   
45542       45543     3977  2019122915       SEA        SF     SEA   
45543       45544     3999  2019122915       SEA        SF     SEA   
45544       45545     4080  2019122915       SEA        SF      SF   
45545       45546     4101  2019122915       SEA        SF     NaN   

      posteam_type defteam side_of_field  yardline_100   game_date  \
0             away     CHI           CHI          35.0  2019-09-05   
1             away     CHI            GB          75.0  2019-09-05   
2             away     CHI            GB          75.0  2019-09-05   
3             away     CHI            GB          75.0  2019-09-05   
4             away     CHI            GB          85.0  2019-09-05   
...            ...     ...           ...           ...         ...   
45541         home      SF            SF           5.0  2019-12-29   
45542         home      SF            SF           5.0  2019-12-29   
45543         home      SF            SF           5.0  2019-12-29   
45544         away     SEA            SF          99.0  2019-12-29   
45545          NaN     NaN            SF           NaN  2019-12-29   

       quarter_seconds_remaining  half_seconds_remaining  \
0                          900.0                  1800.0   
1                          900.0                  1800.0   
2                          873.0                  1773.0   
3                          825.0                  1725.0   
4                          795.0                  1695.0   
...                          ...                     ...   
45541                       22.0                    22.0   
45542                       15.0                    15.0   
45543                       12.0                    12.0   
45544                        9.0                     9.0   
45545                        0.0                     0.0   

       game_seconds_remaining game_half  quarter_end  drive  sp  qtr  down  \
0                      3600.0     Half1            0      1   0    1   NaN   
1                      3600.0     Half1            0      1   0    1   1.0   
2                      3573.0     Half1            0      1   0    1   2.0   
3                      3525.0     Half1            0      1   0    1   3.0   
4                      3495.0     Half1            0      1   0    1   4.0   
...                       ...       ...          ...    ...  ..  ...   ...   
45541                    22.0     Half2            0     16   0    4   2.0   
45542                    15.0     Half2            0     16   0    4   3.0   
45543                    12.0     Half2            0     16   0    4   4.0   
45544                     9.0     Half2            0     17   0    4   1.0   
45545                     0.0     Half2            1     17   0    4   NaN   

       goal_to_go   time   yrdln  ydstogo  ydsnet  \
0             0.0  15:00  CHI 35        0     -10   
1             0.0  15:00   GB 25       10     -10   
2             0.0  14:33   GB 25       10     -10   
3             0.0  13:45   GB 25       10     -10   
4             0.0  13:15   GB 15       20     -10   
...           ...    ...     ...      ...     ...   
45541         1.0  00:22    SF 5        5      72   
45542         1.0  00:15    SF 5        5      72   
45543         1.0  00:12    SF 5        5      72   
45544         0.0  00:09    SF 1       10       2   
45545         NaN  00:00    SF 1        0       2   

                              

In [89]:
pd.set_option('display.max_rows',None)

RB_stats = df[df['play_type'] == 'run'].groupby(['play_maker', 'posteam', 'week', 'Zone'], as_index = False).agg({
    'yards_gained':['sum', 'count'],
    'rush_touchdown':['sum'],
    
})


RB_stats.columns = ['play_maker', 'player_team', 'Week', 'Zone', 'Rush_Yards', 'rush_attempts', 'rush_touchdown']
RB_list = RB_stats.play_maker.unique()
RB_stats

play_maker player_team  Week          Zone  Rush_Yards  \
0             A.Abdullah         MIN     1         Other           8   
1             A.Abdullah         MIN     2         Other           2   
2             A.Abdullah         MIN     5         Other          25   
3             A.Abdullah         MIN     5      Red Zone          -1   
4             A.Abdullah         MIN     9         Other           2   
5             A.Abdullah         MIN    11         Other           5   
6             A.Abdullah         MIN    15         Other          25   
7             A.Abdullah         MIN    16         Other          27   
8             A.Abdullah         MIN    17         Other           8   
9             A.Abdullah         MIN    17      Red Zone          14   
10               A.Armah         CAR     1  Inside the 5           1   
11               A.Armah         CAR     3         Other           4   
12               A.Armah         CAR     6         Other           4   
13               A.Armah         CAR    12  Inside the 5           0   
14               A.Armah         CAR    13         Other           2   
15                A.Beck         DEN    16         Other           3   
16               A.Brown          NE     2         Other           5   
17               A.Brown         TEN     7         Other          -2   
18               A.Brown         TEN    14         Other          13   
19               A.Brown         TEN    16         Other          49   
20              A.Cooper         DAL    17         Other           6   
21              A.Dalton         CIN     2         Other           2   
22              A.Dalton         CIN     3  Inside the 5           1   
23              A.Dalton         CIN     4         Other           8   
24              A.Dalton         CIN     5         Other           0   
25              A.Dalton         CIN     5      Red Zone           5   
26              A.Dalton         CIN     6  Inside the 5           2   
27              A.Dalton         CIN     7  Inside the 5           1   
28              A.Dalton         CIN     7         Other          32   
29              A.Dalton         CIN     8         Other           4   
30              A.Dalton         CIN    13         Other           2   
31              A.Dalton         CIN    14  Inside the 5           2   
32              A.Dalton         CIN    14         Other           6   
33              A.Dalton         CIN    14      Red Zone           3   
34              A.Dalton         CIN    15         Other           2   
35              A.Dalton         CIN    16  Inside the 5           2   
36              A.Dalton         CIN    17  Inside the 5           5   
37              A.Dalton         CIN    17         Other          10   
38              A.Ekeler         LAC     1         Other          52   
39              A.Ekeler         LAC     1      Red Zone           6   
40              A.Ekeler         LAC     2  Inside the 5           1   
41              A.Ekeler         LAC     2         Other          65   
42              A.Ekeler         LAC     3         Other          32   
43              A.Ekeler         LAC     3      Red Zone           4   
44              A.Ekeler         LAC     4  Inside the 5           2   
45              A.Ekeler         LAC     4         Other          58   
46              A.Ekeler         LAC     5         Other           7   
47              A.Ekeler         LAC     6         Other          14   
48              A.Ekeler         LAC     7         Other           7   
49              A.Ekeler         LAC     7      Red Zone           0   
50              A.Ekeler         LAC     8  Inside the 5           0   
51              A.Ekeler         LAC     8         Other           0   
52              A.Ekeler         LAC     8      Red Zone           3   
53              A.Ekeler         LAC     9  Inside the 5           4   
54              A.Ekeler         LAC     9         Oth

In [91]:
RB2_stats = df[(df['play_type'] == 'reception')].groupby(['play_maker', 'posteam', 'week', 'Zone'], as_index = False).agg({
    'yards_gained':['sum'],
    'pass_touchdown':['sum'],
    'reception':['sum'],
    'Target':['sum']
    
})

RB2_stats.columns = ['play_maker', 'player_team', 'Week', 'Zone', 'Rec_Yards', 'pass_touchdown', 'Rec', 'Tgt']

In [82]:
final_RB = RB_stats.merge(RB2_stats, on = ['play_maker', 'player_team', 'Week', 'Zone'], how = 'left')

In [90]:
final_RB

play_maker player_team  Week          Zone  Yards  Long  \
0             A.Abdullah         MIN     1         Other      8     6   
1             A.Abdullah         MIN     2         Other      2     2   
2             A.Abdullah         MIN     5         Other     25    15   
3             A.Abdullah         MIN     5      Red Zone     -1    -1   
4             A.Abdullah         MIN     9         Other      2     2   
5             A.Abdullah         MIN    11         Other      5     5   
6             A.Abdullah         MIN    15         Other     25    11   
7             A.Abdullah         MIN    16         Other     27    14   
8             A.Abdullah         MIN    17         Other      8     3   
9             A.Abdullah         MIN    17      Red Zone     14    11   
10               A.Armah         CAR     1  Inside the 5      1     1   
11               A.Armah         CAR     3         Other      4     4   
12               A.Armah         CAR     6         Other      4     3   
13               A.Armah         CAR    12  Inside the 5      0     0   
14               A.Armah         CAR    13         Other      2     2   
15                A.Beck         DEN    16         Other      3     3   
16               A.Brown          NE     2         Other      5     5   
17               A.Brown         TEN     7         Other     -2    -2   
18               A.Brown         TEN    14         Other     13    13   
19               A.Brown         TEN    16         Other     49    49   
20              A.Cooper         DAL    17         Other      6     6   
21              A.Dalton         CIN     2         Other      2     2   
22              A.Dalton         CIN     3  Inside the 5      1     1   
23              A.Dalton         CIN     4         Other      8     4   
24              A.Dalton         CIN     5         Other      0     0   
25              A.Dalton         CIN     5      Red Zone      5     5   
26              A.Dalton         CIN     6  Inside the 5      2     2   
27              A.Dalton         CIN     7  Inside the 5      1     1   
28              A.Dalton         CIN     7         Other     32    17   
29              A.Dalton         CIN     8         Other      4     4   
30              A.Dalton         CIN    13         Other      2     2   
31              A.Dalton         CIN    14  Inside the 5      2     2   
32              A.Dalton         CIN    14         Other      6     6   
33              A.Dalton         CIN    14      Red Zone      3     3   
34              A.Dalton         CIN    15         Other      2     2   
35              A.Dalton         CIN    16  Inside the 5      2     2   
36              A.Dalton         CIN    17  Inside the 5      5     5   
37              A.Dalton         CIN    17         Other     10     7   
38              A.Ekeler         LAC     1         Other     52    19   
39              A.Ekeler         LAC     1      Red Zone      6     7   
40              A.Ekeler         LAC     2  Inside the 5      1     2   
41              A.Ekeler         LAC     2         Other     65    12   
42              A.Ekeler         LAC     3         Other     32    11   
43              A.Ekeler         LAC     3      Red Zone      4     4   
44              A.Ekeler         LAC     4  Inside the 5      2     1   
45              A.Ekeler         LAC     4         Other     58     9   
46              A.Ekeler         LAC     5         Other      7     4   
47              A.Ekeler         LAC     6         Other     14    11   
48              A.Ekeler         LAC     7         Other      7     3   
49              A.Ekeler         LAC     7      Red Zone      0     0   
50              A.Ekeler         LAC     8  Inside the 5      0     0   
51              A.Ekeler         LAC     8         Other      0     0   
52              A.Ekeler         LAC     8      Red Zone      3     3   
53              A.Ekeler         LAC     9  Inside the 5      4     3   

In [85]:
final_RB.to_csv('RB_Zones.csv')